In [1]:
%matplotlib inline

# Función que genera regresión y periodograma

In [2]:
import datetime
import matplotlib.pyplot as plt
import typing

import altair as alt
import pandas as pd
import numpy as np
from scipy import signal
from sklearn.linear_model import LinearRegression

alt.data_transformers.disable_max_rows()


def regresion_y_periodograma(
    df: pd.DataFrame,
    sampling_rate: int,
    time_format: str,
    x_range: list = [0, 2.5],
    period: str = "días",
):
    """Simple Función para graficar serie de tiempo junto con una regresión lineal"""
    # Primero convertimos los datos de serie de tiempo a timestamp
    df["timestamp"] = df["ds"].apply(
        lambda x: datetime.datetime.timestamp(
            datetime.datetime.strptime(x, time_format)
        )
    )

    # Comenzaremos a contar desde 0 y lo escalaremos a segundos
    df["timestamp_shifted"] = (df["timestamp"] - df["timestamp"][0]) / 60
    df_x = df.dropna().copy()

    # Transformación necesaria para utilizar el módulo de regresión de SciKitLearn
    X = np.array(df_x["timestamp_shifted"]).reshape(-1, 1)

    # La señal dependerá de cada serie de tiempo (e.g. Temperatura cad 5 minutos)
    y = df_x["y"]

    # Hacemos la regresión
    model = LinearRegression()
    model.fit(X, y)

    # Hacemos prediciones sobre los datos observados para "dibujar" la regresión
    df_x.loc[:, "pred_signal_linreg"] = model.predict(X)

    # Capturamos los residuales
    df_x.loc[:, "residuals"] = df_x["y"] - df_x["pred_signal_linreg"]

    # Utilizaremos Altair para graficar la regresión y la serie de tiempo
    scatter = (
        alt.Chart(df_x)
        .mark_circle(opacity=0.4, color="black")
        .encode(
            x="timestamp_shifted",
            y="y",
        )
    )

    regression_plot = (
        alt.Chart(df_x)
        .mark_line(color="#fdbf11")
        .encode(x="timestamp_shifted", y="pred_signal_linreg")
    )

    print("Slope: {:.2e}, Intercept: {:.2f}".format(model.coef_[0], model.intercept_))
    print("R-squared: {:.2e}".format(model.score(X, y)))

    fs = sampling_rate

    f, Pxx_den = signal.periodogram(y, fs)

    list_of_tuples = list(zip(f, Pxx_den))
    df = pd.DataFrame(list_of_tuples, columns=["f", "Power Spectral Density"])

    periodograma = (
        alt.Chart(df)
        .mark_line(opacity=1, color="#fdbf11", point=True)
        .encode(
            x=alt.X(
                "f",
                scale=alt.Scale(domain=x_range, clamp=True),
                axis=alt.Axis(title=f"Periodo ({period})"),
            ),
            y=alt.Y("Power Spectral Density"),
        )
    )

    return (scatter + regression_plot) | periodograma


/home/oswaldo/.cache/pypoetry/virtualenvs/timeseriesmaster-BrJHQkVI-py3.8/lib/python3.8/site-packages/pandas/compat/__init__.py:97: UserWarning: Could not import the lzma module. Your installed Python is incomplete. Attempting to use lzma compression will result in a RuntimeError.
  warnings.warn(msg)


# 1 Peyton Manning

Serie de tiempo de el número de vistas de la página de Wikipedia de Peyton Manning. Originalmente se utilizó el paquete Wikipediatrend de R. Esto provee un ejemplo muy claro de las características de prophet como múltiple estacionalidad, tasas cambiantes, y la habilidad del modelo para los días especiales (es decir los días de playoff o superbowl).

In [3]:
data1=pd.read_csv('../data/examples/example_wp_log_peyton_manning.csv')
data1.head()

ds         y
0  2007-12-10  9.590761
1  2007-12-11  8.519590
2  2007-12-12  8.183677
3  2007-12-13  8.072467
4  2007-12-14  7.893572

In [4]:
# Sampling_rate en número de días por año
regresion_y_periodograma(data1,sampling_rate=365,time_format="%Y-%m-%d",period='años') 

Slope: 4.34e-08, Intercept: 8.05
R-squared: 3.96e-03


alt.HConcatChart(...)

## Interpretabilidad

Aquí podemos ver que cada año aproximadamente suben las búsquedas relacionadas con Peyton Manning, lo qu se puede explicar con la periodicidad del Super Bowl y de los PlayOffs

# 2

La serie de tiempo del número de pasajeros aereos es un ejemplo cuando la estacionalidad aditiva no funciona. 

In [5]:
data2=pd.read_csv('../data/examples/example_air_passengers.csv')
data2.head()

ds    y
0  1949-01-01  112
1  1949-02-01  118
2  1949-03-01  132
3  1949-04-01  129
4  1949-05-01  121

In [6]:
# Sampling Rate en número de meses por año
regresion_y_periodograma(data2,sampling_rate=12,time_format="%Y-%m-%d",x_range=[0,2],period='años') 

Slope: 6.06e-05, Intercept: 90.42
R-squared: 8.53e-01


alt.HConcatChart(...)

## Interoperabilidad
. 
Vemos que existe una señal alrededor de 0.1 años (30 días). Lo cual quiere decir que el número de pasajeros está correlacionado con el número de pasajero del siguiente mes. 

La señal más sencilla es la de un año. Cada año existe una fuerte periodicidad, lo cual es bastante intuitivo

## Filtro lineal. Promdio móvil

Aquí graficaremos la serie de tiempo suavizada (arriba), tomando como ventana en este caso 50% del total del tamaño de la serie. La serie de diferencias la tenemos debajo.

# 3

Ventas mensuales

In [7]:
data3=pd.read_csv('../data/examples/example_retail_sales.csv')
data3.head(13)

ds       y
0   1992-01-01  146376
1   1992-02-01  147079
2   1992-03-01  159336
3   1992-04-01  163669
4   1992-05-01  170068
5   1992-06-01  168663
6   1992-07-01  169890
7   1992-08-01  170364
8   1992-09-01  164617
9   1992-10-01  173655
10  1992-11-01  171547
11  1992-12-01  208838
12  1993-01-01  153221

In [8]:
# Sampling Rate en número de meses por año
regresion_y_periodograma(data3,sampling_rate=12,time_format="%Y-%m-%d",x_range=[0,1],period='años' ) 

Slope: 2.22e-02, Intercept: 166780.01
R-squared: 9.19e-01


alt.HConcatChart(...)

## Interpretabilidad

    Vemos que aproximadamente cada 14 días (0.04 años) hay cierta periodicidad

# 4

Vemos aquí el creciemiento de las ventas como función del tiempo

In [9]:
data4=pd.read_csv('../data/examples/example_wp_log_R.csv')
data4=data4.sort_values('ds').reset_index(drop=True)
data4

ds         y
0     2008-01-01  4.804021
1     2008-01-02  5.379897
2     2008-01-03  5.659482
3     2008-01-04  5.598422
4     2008-01-05  5.278115
...          ...       ...
2858  2015-12-27  7.040536
2859  2015-12-28  7.564238
2860  2015-12-29  7.604396
2861  2015-12-30  7.612831
2862  2015-12-31  7.236339

[2863 rows x 2 columns]

In [10]:
regresion_y_periodograma(data4,sampling_rate=365,time_format="%Y-%m-%d",x_range=[0,1],period='años') 

Slope: 4.75e-07, Intercept: 6.10
R-squared: 7.21e-01


alt.HConcatChart(...)

## Interpretabilidad

Parece interesante que exista una frecuencia alrededor de 0.12 que corresponde aproximadamente a 1.5 meses. Quizas tenga que ver con principios de temporada y rebajas. 


# 5  

Aquí tenemos datos con resolución de 5 minutos (temperatura diaria en Yosemite).

In [11]:
import datetime
import matplotlib.pyplot as plt

import altair as alt
import pandas as pd
import numpy as np
from scipy import signal
from sklearn.linear_model import LinearRegression

data5=pd.read_csv('../data/examples/example_yosemite_temps.csv')
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [12]:
data5=pd.read_csv('../data/examples/example_yosemite_temps.csv')
# Como la frecuencia es de 5 minutos. Dejemos la frecuencia en días (288 intervalos de 5 minutos = 1 día)
regresion_y_periodograma(data5,sampling_rate=288,time_format="%Y-%m-%d %H:%M:%S") 


Slope: 1.54e-04, Intercept: 11.24
R-squared: 8.98e-02


alt.HConcatChart(...)

## Interpretabilidad

Logramos observer que existe una frecuencia asociada a un día. Lo cual resulta bastante intuitivo considerar que normalemente se repite la misma temperatura al día siguiente e incluso logramos observar que las temperaturas cercanas al punto inicial también están asociadas. 

Finalmente Vemos que a menor medida, la temperatura se repite 2 días después